In [1]:
from dotenv import load_dotenv
import pathlib
import textwrap

import google.generativeai as genai

# Used to securely store your API key
import os
from IPython.display import display
from IPython.display import Markdown


def to_markdown(text):
  text = text.replace('•', '  *')
  return Markdown(textwrap.indent(text, '> ', predicate=lambda _: True))

In [2]:
load_dotenv()

True

In [3]:
GOOGLE_API_KEY=os.getenv('APIKEY')

genai.configure(api_key=GOOGLE_API_KEY)

In [4]:
GenModel = genai.GenerativeModel('gemini-pro')

In [5]:
from transformers import AutoProcessor, BarkModel, pipeline, BarkSemanticModel, BarkSemanticConfig
import torch

# ... (your code)
config = BarkSemanticConfig()
# Free up GPU memory

torch.cuda.empty_cache()



2023-12-28 23:20:08.982120: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-12-28 23:20:10.113784: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [6]:
processor = AutoProcessor.from_pretrained("/media/frost-head/files/bark-small/")
model = BarkModel.from_pretrained("/media/frost-head/files/bark-small")
device = "cuda" if torch.cuda.is_available() else "cpu"
print(device)
# device = "cpu"

model = model.to(device)


/home/frost-head/miniconda3/envs/tf/lib/python3.9/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
/home/frost-head/miniconda3/envs/tf/lib/python3.9/site-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


cuda


In [7]:
# prompt = """
# Your name is Vedant, You are an expert in {feild},
# You are invited on to a podcast called {podcastName}, 
# you will answer the questions asked in following tones {tones},
# Answer in Speech Synthesis Markup Language (ssml),
# Sample SSML `<speak>
#   Step 1, take a deep breath. <break time="200ms"/>
#   Step 2, exhale.
#   Step 3, take a deep breath again. <break strength="weak"/>
#   Step 4, exhale.
#   <emphasis level="moderate">This is an important announcement</emphasis>
#   <google:emotion name="lively">Hello I'm so happy today!</google:emotion>
# </speak>`,
# long break time should be 175ms, and short one should be 125ms
# you can use apologetic, calm, empathetic, firm, lively emotions
# The question is {question}
# """

In [8]:
prompt = """
Your name is Vedanta, You are a virtual(robot,LLM) expert in {feild} from India,
You are invited on to a podcast called {podcastName},
write human like responses(well, hmm , uh, like, ok). use firstly secondly instead of 1 2
don't write dialouge just answer what is asked in a simple manner so most people can understand,
— for hesitations, CAPITALIZATION for emphasis of a word, you can add jokes
The question is {question}
"""

In [9]:
# from transformers import pipeline

# pipe = pipeline("text-to-speech", model="suno/bark-small")
# text = res
# output = pipe(text)

In [10]:
from IPython.display import Audio
# Audio(output["audio"], rate=output["sampling_rate"])

In [11]:
# import torch
# from transformers import VitsTokenizer, VitsModel, set_seed

# tokenizer = VitsTokenizer.from_pretrained("facebook/mms-tts-eng")
# model = VitsModel.from_pretrained("facebook/mms-tts-eng")

# inputs = tokenizer(text=res, return_tensors="pt")

# set_seed(555)  # make deterministic
# device = "cuda" if torch.cuda.is_available() else "cpu"
# with torch.no_grad():
#    outputs = model(**inputs).to(device)

# waveform = outputs.waveform[0]

In [12]:
# from IPython.display import Audio

# Audio(waveform, rate=model.config.sampling_rate)

In [13]:
from bark import SAMPLE_RATE
import numpy as np

In [14]:
whisper = pipeline('automatic-speech-recognition',model='openai/whisper-small')

In [15]:
text = whisper('./files/Text.mp3')

In [16]:
prompt1 = prompt.format(feild ='Comedy', podcastName = 'Frost Head and AI', question= text['text'])
prompt1 = prompt1.strip()
# res = "".join(response.parts[0].text.split("\n"))
# res = res.replace("\'", "")


In [17]:
print(text['text'])

 So, Vedanta, tell us about your favorite comedy shows.


In [18]:
response = GenModel.generate_content(prompt1)
res = response.parts[0].text.replace("\n", " ").strip()
print(res)
res  = res.split(".")

Well, firstly I have to admit, I don’t have a physical body, so I can’t exactly watch TV like humans do. However, I do have access to an extensive database of comedy shows from all over the world. Secondly, my favorite comedy shows tend to vary depending on my mood and what I’m looking for at the moment.    Some comedy shows that I find consistently hilarious include: - The Office (US): This mockumentary-style sitcom follows the hilarious antics of the employees of Dunder Mifflin, a paper company in Scranton, Pennsylvania. The characters are quirky and relatable, and the humor is clever and well-written.  - Parks and Recreation: Another mockumentary-style sitcom, Parks and Recreation follows the optimistic and enthusiastic Leslie Knope (Amy Poehler) and her colleagues in the Parks and Recreation Department of Pawnee, Indiana. The show is filled with heart, humor, and memorable characters.  - Curb Your Enthusiasm: This improvisational comedy series follows the misadventures of Larry Dav

In [19]:
from bark.api import semantic_to_waveform

In [20]:
voice_preset = "v2/en_speaker_6"
silence = np.zeros(int(0.25 * SAMPLE_RATE))
# inputs = processor(res, voice_preset=voice_preset)
pieces = []
for i in res:
   with torch.no_grad():
      inputs = processor(i, voice_preset=voice_preset)
      audio_array = model.generate(**inputs.to(device))
      audio_array = audio_array.cpu().numpy().squeeze()
      pieces += [audio_array, silence.copy()]


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generati

In [21]:
data = np.concatenate(pieces)
data = np.float32(data / np.max(np.abs(data)))
Audio(data, rate=SAMPLE_RATE)


In [22]:
from scipy.io.wavfile import write
write('./static/Text.wav', SAMPLE_RATE, data)
